In [16]:
import pandas as pd
import os
import datetime
import glob
import pickle 
import json
from zipfile import ZipFile
from io import TextIOWrapper

In [4]:
import re
import sys
from numbers import Number

import six

ERRORS = {
    'unexp_end_string': u'Unexpected end of string while parsing Lua string.',
    'unexp_end_table': u'Unexpected end of table while parsing Lua string.',
    'mfnumber_minus': u'Malformed number (no digits after initial minus).',
    'mfnumber_dec_point': u'Malformed number (no digits after decimal point).',
    'mfnumber_sci': u'Malformed number (bad scientific format).',
}

def sequential(lst):
    length = len(lst)
    if length == 0 or lst[0] != 0:
        return False
    for i in range(length):
        if i + 1 < length:
            if lst[i] + 1 != lst[i+1]:
                return False
    return True


class ParseError(Exception):
    pass


class SLPP(object):

    def __init__(self):
        self.text = ''
        self.ch = ''
        self.at = 0
        self.len = 0
        self.depth = 0
        self.space = re.compile('\s', re.M)
        self.alnum = re.compile('\w', re.M)
        self.newline = '\n'
        self.tab = '\t'

    def decode(self, text):
        if not text or not isinstance(text, six.string_types):
            return
        # FIXME: only short comments removed
        reg = re.compile('--.*$', re.M)
        text = reg.sub('', text, 0)
        self.text = text
        self.at, self.ch, self.depth = 0, '', 0
        self.len = len(text)
        self.next_chr()
        result = self.value()
        return result

    def encode(self, obj):
        self.depth = 0
        return self.__encode(obj)

    def __encode(self, obj):
        s = ''
        tab = self.tab
        newline = self.newline

        if isinstance(obj, str):
            s += '"%s"' % obj.replace(r'"', r'\"')
        elif six.PY2 and isinstance(obj, unicode):
            s += '"%s"' % obj.encode('utf-8').replace(r'"', r'\"')
        elif six.PY3 and isinstance(obj, bytes):
            s += '"{}"'.format(''.join(r'\x{:02x}'.format(c) for c in obj))
        elif isinstance(obj, bool):
            s += str(obj).lower()
        elif obj is None:
            s += 'nil'
        elif isinstance(obj, Number):
            s += str(obj)
        elif isinstance(obj, (list, tuple, dict)):
            self.depth += 1
            if len(obj) == 0 or (not isinstance(obj, dict) and len([
                    x for x in obj
                    if isinstance(x, Number) or (isinstance(x, six.string_types) and len(x) < 10)
               ]) == len(obj)):
                newline = tab = ''
            dp = tab * self.depth
            s += "%s{%s" % (tab * (self.depth - 2), newline)
            if isinstance(obj, dict):
                key = '[%s]' if all(isinstance(k, (int, long)) for k in obj.keys()) else '%s'
                contents = [dp + (key + ' = %s') % (k, self.__encode(v)) for k, v in obj.items()]
                s += (',%s' % newline).join(contents)
            else:
                s += (',%s' % newline).join(
                    [dp + self.__encode(el) for el in obj])
            self.depth -= 1
            s += "%s%s}" % (newline, tab * self.depth)
        return s

    def white(self):
        while self.ch:
            if self.space.match(self.ch):
                self.next_chr()
            else:
                break

    def next_chr(self):
        if self.at >= self.len:
            self.ch = None
            return None
        self.ch = self.text[self.at]
        self.at += 1
        return True

    def value(self):
        self.white()
        if not self.ch:
            return
        if self.ch == '{':
            return self.object()
        if self.ch == "[":
            self.next_chr()
        if self.ch in ['"',  "'",  '[']:
            return self.string(self.ch)
        if self.ch.isdigit() or self.ch == '-':
            return self.number()
        return self.word()

    def string(self, end=None):
        s = ''
        start = self.ch
        if end == '[':
            end = ']'
        if start in ['"',  "'",  '[']:
            while self.next_chr():
                if self.ch == end:
                    self.next_chr()
                    if start != "[" or self.ch == ']':
                        return s
                if self.ch == '\\' and start == end:
                    self.next_chr()
                    if self.ch != end:
                        s += '\\'
                s += self.ch
        raise ParseError(ERRORS['unexp_end_string'])

    def object(self):
        o = {}
        k = None
        idx = 0
        numeric_keys = False
        self.depth += 1
        self.next_chr()
        self.white()
        if self.ch and self.ch == '}':
            self.depth -= 1
            self.next_chr()
            return o  # Exit here
        else:
            while self.ch:
                self.white()
                if self.ch == '{':
                    o[idx] = self.object()
                    idx += 1
                    continue
                elif self.ch == '}':
                    self.depth -= 1
                    self.next_chr()
                    if k is not None:
                        o[idx] = k
                    if len([key for key in o if isinstance(key, six.string_types + (float,  bool, tuple))]) == 0:
                        so = sorted([key for key in o])
                        if sequential(so):
                            ar = []
                            for key in o:
                                ar.insert(key, o[key])
                            o = ar
                    return o  # or here
                else:
                    if self.ch == ',':
                        self.next_chr()
                        continue
                    else:
                        k = self.value()
                        if self.ch == ']':
                            self.next_chr()
                    self.white()
                    ch = self.ch
                    if ch in ('=', ','):
                        self.next_chr()
                        self.white()
                        if ch == '=':
                            o[k] = self.value()
                        else:
                            o[idx] = k
                        idx += 1
                        k = None
        raise ParseError(ERRORS['unexp_end_table'])  # Bad exit here

    words = {'true': True, 'false': False, 'nil': None}
    def word(self):
        s = ''
        if self.ch != '\n':
            s = self.ch
        self.next_chr()
        while self.ch is not None and self.alnum.match(self.ch) and s not in self.words:
            s += self.ch
            self.next_chr()
        return self.words.get(s, s)

    def number(self):
        def next_digit(err):
            n = self.ch
            self.next_chr()
            if not self.ch or not self.ch.isdigit():
                raise ParseError(err)
            return n
        n = ''
        try:
            if self.ch == '-':
                n += next_digit(ERRORS['mfnumber_minus'])
            n += self.digit()
            if n == '0' and self.ch in ['x', 'X']:
                n += self.ch
                self.next_chr()
                n += self.hex()
            else:
                if self.ch and self.ch == '.':
                    n += next_digit(ERRORS['mfnumber_dec_point'])
                    n += self.digit()
                if self.ch and self.ch in ['e', 'E']:
                    n += self.ch
                    self.next_chr()
                    if not self.ch or self.ch not in ('+', '-'):
                        raise ParseError(ERRORS['mfnumber_sci'])
                    n += next_digit(ERRORS['mfnumber_sci'])
                    n += self.digit()
        except ParseError:
            t, e = sys.exc_info()[:2]
            print(e)
            return 0
        try:
            return int(n, 0)
        except:
            pass
        return float(n)

    def digit(self):
        n = ''
        while self.ch and self.ch.isdigit():
            n += self.ch
            self.next_chr()
        return n

    def hex(self):
        n = ''
        while self.ch and (self.ch in 'ABCDEFabcdef' or self.ch.isdigit()):
            n += self.ch
            self.next_chr()
        return n


slpp = SLPP()

__all__ = ['slpp']

In [52]:
with ZipFile('MMDataTest.zip','r') as zf:
    name = zf.namelist()[0]
    print(name)
    data = zf.open(name,'r').read().decode('utf8')
    

MM00Data.lua


'MM00DataSavedVariables =\r\n{\r\n    ["Default"] = \r\n    {\r\n        ["@TholosTB2"] = \r\n        {\r\n            ["$AccountWide"] = \r\n            {\r\n                ["version"] = 1,\r\n            },\r\n        },\r\n        ["MasterMerchant"] = \r\n        {\r\n            ["$AccountWide"] = \r\n            {\r\n                ["version"] = 1,\r\n                ["SalesData"] = \r\n                {\r\n                    [99330] = \r\n                    {\r\n                        ["50:16:4:3:0"] = \r\n                        {\r\n                            ["itemIcon"] = "/esoui/art/icons/gear_redguard_2hsword_d.dds",\r\n                            ["sales"] = \r\n                            {\r\n                                [1] = \r\n                                {\r\n                                    ["seller"] = "@septum83.12348",\r\n                                    ["buyer"] = "@marrowmeiser",\r\n                                    ["guild"] = "Imperfect 

In [53]:
salesdatMM = slpp.decode(data.split('=',1))

In [54]:
salesdatMM

In [3]:
all_sales = []
for f in glob.glob('c:/users/jtern/documents/elder scrolls online/live/savedvariables/arkadiusTradeToolsSalesData*.lua'):
    salesdata = open(f,'r').read()
    sales = slpp.decode(salesdata.split('=',1)[1])
    na = sales['NA Megaserver']['sales']
    all_sales.extend(na.values())

In [4]:
all_sales[-1]

{'internal': 0,
 'taxes': 14,
 'buyerName': '@benashey',
 'quantity': 1,
 'itemLink': '|H0:item:45356:365:50:0:0:0:0:0:0:0:0:0:0:0:0:19:0:0:0:10000:0|h|h',
 'timeStamp': 1632628194,
 'guildName': 'Imperfect Cleave',
 'sellerName': '@Schaffino',
 'price': 420}

In [5]:
sales_df = pd.DataFrame(all_sales)

In [13]:
with open('c:/users/jtern/documents/github/eso_motifs/itemdb.json','r') as f:
    new_item_db = json.load(f)

In [14]:
sales_df['sale_ts'] = sales_df['timeStamp'].apply(datetime.datetime.fromtimestamp)
sales_df['item_id'] = sales_df['itemLink'].apply(lambda r : r.split(":")[2])
sales_df['item_name'] = sales_df['item_id'].apply(lambda r : new_item_db.get(r,''))

In [26]:
sales_df['week_period'] = sales_df['sale_ts'].dt.to_period('W-WED')

In [27]:
sales_df['unitPrice'] = sales_df.apply(lambda r : r['price']/r['quantity'] if pd.isna(r['unitPrice']) else r['unitPrice'],axis=1)

In [16]:
master_sales_df = pd.read_pickle('c:/users/jtern/documents/github/eso_motifs/sales_data.pickle')

In [28]:
new_master_sales_df = pd.concat([master_sales_df,sales_df], axis=0)

In [29]:
new_master_sales_df.head()

buyerName   timeStamp  taxes  quantity  price  internal  sellerName  \
0      @mandrew0822  1631795739    280         1   8000         0  @txeptirea   
1         @kounoike  1630144306     62       200   1795         0   @Tmantosa   
2           @Morunn  1631903273     70       200   2015         0    @Euphorb   
3  @bradleymsimmons  1629787627      6         1    184         0    @kasp362   
4    @Reydealemania  1631241311     35         1   1000         1    @seageek   

          guildName                                           itemLink  \
0  Imperfect Cleave  |H0:item:180899:362:50:0:0:0:0:0:0:0:0:0:0:0:0...   
1  Imperfect Cleave  |H0:item:64489:30:1:0:0:0:0:0:0:0:0:0:0:0:0:0:...   
2  Imperfect Cleave  |H0:item:64502:30:1:0:0:0:0:0:0:0:0:0:0:0:0:0:...   
3  Imperfect Cleave  |H0:item:68224:4:1:0:0:0:0:0:0:0:0:0:0:0:0:0:0...   
4  Imperfect Cleave  |H0:item:71679:5:1:0:0:0:0:0:0:0:0:0:0:0:0:0:0...   

   unitPrice             sale_ts item_id                          item_name  \
0   8000.000 2021-09-16 07:35:39  180899                  Hrothgar's Shield   
1      8.975 2021-08-28 04:51:46   64489                     Rubedite Ingot   
2     10.075 2021-09-17 13:27:53   64502                    Sanded Ruby Ash   
3    184.000 2021-08-24 01:47:07   68224    Recipe: Camlorn Sweet Brown Ale   
4   1000.000 2021-09-09 21:35:11   71679  Crafting Motif 28: Ra Gada Gloves   

             week_period  
0  2021-09-16/2021-09-22  
1  2021-08-26/2021-09-01  
2  2021-09-16/2021-09-22  
3  2021-08-19/2021-08-25  
4  2021-09-09/2021-09-15

In [30]:
new_master_sales_df.loc[new_master_sales_df.duplicated(keep=False)].sort_values(['timeStamp','sellerName','item_id'])

buyerName   timeStamp  taxes  quantity  price  internal  \
33598        @aj199506  1629733162      4         1    115         0   
37629        @aj199506  1629733162      4         1    115         0   
23144  @Emperor_Mather  1629736645    386       200  11036         0   
41594  @Emperor_Mather  1629736645    386       200  11036         0   
13143  @Emperor_Mather  1629736647    387       200  11074         0   
...                ...         ...    ...       ...    ...       ...   
21947       @akafuji88  1633003774    924         1  26400         0   
22203         @Terzeth  1633009412     43         1   1250         0   
37371         @Terzeth  1633009412     43         1   1250         0   
31420         @Terzeth  1633009418     52         1   1500         0   
46696         @Terzeth  1633009418     52         1   1500         0   

                sellerName         guildName  \
33598         @CrystalDuck  Imperfect Cleave   
37629         @CrystalDuck  Imperfect Cleave   
23144  @picklericklewiggle  Imperfect Cleave   
41594  @picklericklewiggle  Imperfect Cleave   
13143     @MaximumHardship  Imperfect Cleave   
...                    ...               ...   
21947            @Artenion  Imperfect Cleave   
22203            @Toadfang  Imperfect Cleave   
37371            @Toadfang  Imperfect Cleave   
31420      @Mephystopheles  Imperfect Cleave   
46696      @Mephystopheles  Imperfect Cleave   

                                                itemLink  unitPrice  \
33598  |H0:item:26589:309:50:0:0:0:0:0:0:0:0:0:0:0:0:...     115.00   
37629  |H0:item:26589:309:50:0:0:0:0:0:0:0:0:0:0:0:0:...     115.00   
23144  |H0:item:71198:30:1:0:0:0:0:0:0:0:0:0:0:0:0:0:...      55.18   
41594  |H0:item:71198:30:1:0:0:0:0:0:0:0:0:0:0:0:0:0:...      55.18   
13143  |H0:item:71198:30:1:0:0:0:0:0:0:0:0:0:0:0:0:0:...      55.37   
...                                                  ...        ...   
21947  |H0:item:56863:30:1:0:0:0:0:0:0:0:0:0:0:0:0:0:...   26400.00   
22203  |H0:item:138797:365:50:0:0:0:0:0:0:0:0:0:0:0:0...    1250.00   
37371  |H0:item:138797:365:50:0:0:0:0:0:0:0:0:0:0:0:0...    1250.00   
31420  |H0:item:138797:365:50:0:0:0:0:0:0:0:0:0:0:0:0...    1500.00   
46696  |H0:item:138797:365:50:0:0:0:0:0:0:0:0:0:0:0:0...    1500.00   

                  sale_ts item_id        item_name            week_period  
33598 2021-08-23 10:39:22   26589                   2021-08-19/2021-08-25  
37629 2021-08-23 10:39:22   26589                   2021-08-19/2021-08-25  
23144 2021-08-23 11:37:25   71198     Rubedite Ore  2021-08-19/2021-08-25  
41594 2021-08-23 11:37:25   71198     Rubedite Ore  2021-08-19/2021-08-25  
13143 2021-08-23 11:37:27   71198     Rubedite Ore  2021-08-19/2021-08-25  
...                   ...     ...              ...                    ...  
21947 2021-09-30 07:09:34   56863  Potent Nirncrux  2021-09-30/2021-10-06  
22203 2021-09-30 08:43:32  138797  Pewter Necklace  2021-09-30/2021-10-06  
37371 2021-09-30 08:43:32  138797  Pewter Necklace  2021-09-30/2021-10-06  
31420 2021-09-30 08:43:38  138797  Pewter Necklace  2021-09-30/2021-10-06  
46696 2021-09-30 08:43:38  138797  Pewter Necklace  2021-09-30/2021-10-06  

[75457 rows x 14 columns]

In [31]:
new_master_sales_df = new_master_sales_df.drop_duplicates(keep='first')

In [115]:
agg_df = sales_df.groupby(['week_period',"item_id"]).agg({'taxes':'sum','quantity':'sum','price':'sum','item_name' : 'max','unitPrice' : 'mean'}).sort_values('price',ascending=False)
qty_df = sales_df.groupby(['week_period',"item_id"]).agg({'taxes':'sum','quantity':'sum','price':'sum', 'item_name' : 'max', 'unitPrice' : 'mean'}).sort_values('quantity',ascending=False)

In [96]:
sales_df.loc[sales_df['sellerName']=='@TholosTB']

buyerName   timeStamp  taxes  quantity  price  internal  \
135        @gustavo541995  1631499820    276         1   7900         0   
365              @atteres  1630173728   2083        20  59520         0   
1025   @Osiris_Soulreaver  1630251887    355         5  10170         0   
1051         @theskymoves  1631891754    280         4   8000         0   
1476               @ckbud  1629900935    700         1  20000         0   
...                   ...         ...    ...       ...    ...       ...   
48354         @uncanny.gg  1631493805   1750         1  50000         0   
48953         @mrarnold40  1630252549    171         1   4900         0   
50144           @aeleiron  1631111756    875         2  25000         0   
51338         @Fire.Storm  1631329307    210         1   6000         0   
51619           @One_Wish  1631887037   2639        10  75400         1   

      sellerName         guildName  \
135    @TholosTB  Imperfect Cleave   
365    @TholosTB  Imperfect Cleave   
1025   @TholosTB  Imperfect Cleave   
1051   @TholosTB  Imperfect Cleave   
1476   @TholosTB  Imperfect Cleave   
...          ...               ...   
48354  @TholosTB  Imperfect Cleave   
48953  @TholosTB  Imperfect Cleave   
50144  @TholosTB  Imperfect Cleave   
51338  @TholosTB  Imperfect Cleave   
51619  @TholosTB  Imperfect Cleave   

                                                itemLink  unitPrice  \
135    |H0:item:177176:430:1:0:0:0:0:0:0:0:0:0:0:0:0:...     7900.0   
365    |H0:item:151621:30:1:0:0:0:0:0:0:0:0:0:0:0:0:8...     2976.0   
1025   |H0:item:166045:20:1:0:0:0:0:0:0:0:0:0:0:0:0:0...     2034.0   
1051   |H0:item:175725:3:1:0:0:0:0:0:0:0:0:0:0:0:0:0:...     2000.0   
1476   |H0:item:171904:5:1:0:0:0:0:0:0:0:0:0:0:0:0:0:...    20000.0   
...                                                  ...        ...   
48354  |H0:item:178452:124:1:0:0:0:0:0:0:0:0:0:0:0:0:...    50000.0   
48953  |H0:item:147512:363:50:0:0:0:0:0:0:0:0:0:0:0:0...     4900.0   
50144  |H0:item:151770:4:1:0:0:0:0:0:0:0:0:0:0:0:0:0:...    12500.0   
51338  |H0:item:176311:430:1:0:0:0:0:0:0:0:0:0:0:0:0:...     6000.0   
51619  |H0:item:171911:30:1:0:0:0:0:0:0:0:0:0:0:0:0:1...     7540.0   

                  sale_ts item_id                               item_name  
135   2021-09-12 21:23:40  177176                                          
365   2021-08-28 13:02:08  151621                         Shimmering Sand  
1025  2021-08-29 10:44:47  166045                                          
1051  2021-09-17 10:15:54  175725                                          
1476  2021-08-25 09:15:35  171904                                          
...                   ...     ...                                     ...  
48354 2021-09-12 19:43:25  178452  Style Page: Nibenese Court Wizard Robe  
48953 2021-08-29 10:55:49  147512                             Deadly Ring  
50144 2021-09-08 09:35:56  151770                                          
51338 2021-09-10 22:01:47  176311                                          
51619 2021-09-17 08:57:17  171911                     Ivory Brigade Clasp  

[137 rows x 13 columns]

In [101]:
agg_df

taxes  quantity      price           item_name
item_id                                                  
54177    4244668      6348  121284028          Dreugh Wax
135150   3250172       414   92863943    Chromium Plating
54173    1367688      4154   39082292     Tempering Alloy
135149   1362930       533   38943855      Zircon Plating
30145     830981     58827   23746280  Sip of Spell Power
...          ...       ...        ...                 ...
119314         0         1         15                    
119317         0         1         15                    
81237          0         1         15                    
28489          0         2         12                    
45824          0         1          6                    

[9391 rows x 4 columns]

In [49]:
itemdb = {'71198' : "Rubedite Ore", '54177' : 'Dreugh Wax' }

In [69]:
import requests
from bs4 import BeautifulSoup
import time
import random

In [87]:
url = "https://esoitem.uesp.net/itemLink.php?itemid={}&summary"
for itemid in top_items:
    print(itemid)
    if itemid in new_item_db:
        continue
    result = requests.get(url.format(itemid))
    if result.status_code != 200:
        print (f"Error code {result.status_code} sleeping 60")
        time.sleep(60)
        result = requests.get(url.format(itemid))
        if result.status_code != 200:
            print (f"Error code {result.status_code} aborting")
            break
    soup = BeautifulSoup(result.text)
    desc = soup.find(id='esoil_rawdata_name').text
    new_item_db[itemid] = desc
    print (itemid,desc)
    sleeptime = random.randint(0,5)
    print (f"Sleeping {sleeptime}")
    time.sleep(sleeptime)

181565
181565 Blueprint: Leyawiin Turret, Castle
Sleeping 2
181571
181571 Praxis: Leyawiin Wall, Windowed Castle
Sleeping 0
181572
181572 Blueprint: Leyawiin Stairway, Wooden
Sleeping 0
152137
152137 Style Page: the Maelstrom's Shield
Sleeping 4
167305
167305 Runebox: Timbercrow Wanderer Costume
Sleeping 1
150789
150789 Dragon's Bile
Sleeping 5
34311
34311 Apples
Sleeping 0
54173
176725
176725 Companion's Epaulets
Sleeping 5
180465
180465 Gloves of Dark Convergence
Sleeping 1
177030
177030 Companion's Sabatons
Sleeping 4
135141
135141 Silver Dust
Sleeping 3
45851
45851 Jejota
Sleeping 4
115026
115026 Aetherial Dust
Sleeping 5
120078
120078 Diminished Aetherial Dust
Sleeping 5
76843
76843 Enervating Poison I
Sleeping 1
64509
64509 Rejera
Sleeping 0
30357
30357 Lockpick
Sleeping 4
135142
135142 Silver Ounce
Sleeping 2
23121
23121 Sanded Beech
Sleeping 3
77581
77581 Torchbug Thorax
Sleeping 2
26588
33771
33771 Jasmine
Sleeping 1
42862
42862 Trodh
Sleeping 5
181578
181578 Praxis: Leyawiin 

176722
176722 Companion's Hat
Sleeping 2
135161
135161 Ochre
Sleeping 5
33754
33754 White Meat
Sleeping 3
34329
34329 Barley
Sleeping 2
46141
46141 Sanded Mahogany
Sleeping 1
176015
176015 Design: Leyawiin Pie, Octopus
Sleeping 1
175967
175967 Diagram: Leyawiin Sconce, Gilded Lantern
Sleeping 5
46129
46129 Quicksilver Ingot
Sleeping 4
171917
171917 Crafting Motif 102: Sul-Xan Chests
Sleeping 5
180521
180521 Inferno Staff of Dark Convergence
Sleeping 0
45833
45833 Deni
Sleeping 1
45853
45853 Rekuta
Sleeping 5
180502
180502 Lightning Staff of Dark Convergence
Sleeping 0
33755
33755 Bananas
Sleeping 5
34307
34307 Radish
Sleeping 3
135137
135137 Pewter Dust
Sleeping 2
120076
120076 Aetherial Ambrosia
Sleeping 2
170130
170130 Style Page: Thurvokun Mask
Sleeping 4
44879
44879 Grand Repair Kit
Sleeping 4
33774
33774 Yeast
Sleeping 0
173246
173246 Ring of Diamond's Victory
Sleeping 0
139019
139019 Powdered Mother of Pearl
Sleeping 4
139409
139409 Dawn-Prism
Sleeping 3
126848
126848 Praxis: Dwa

In [88]:
new_item_db


{'180899': "Hrothgar's Shield",
 '64489': 'Rubedite Ingot',
 '64502': 'Sanded Ruby Ash',
 '68224': 'Recipe: Camlorn Sweet Brown Ale',
 '71679': 'Crafting Motif 28: Ra Gada Gloves',
 '54177': 'Dreugh Wax',
 '156785': 'Style Page: Legion Zero Sabatons',
 '45350': 'Homespun Hat',
 '45854': 'Kuta',
 '45304': 'Iron Dagger',
 '71198': 'Rubedite Ore',
 '71558': 'Crafting Motif 22: Trinimac Helmets',
 '180765': "Hrothgar's Ring",
 '71576': 'Crafting Motif 23: Malacath Maces',
 '45347': 'Homespun Robe',
 '71200': 'Raw Ancestor Silk',
 '54173': 'Tempering Alloy',
 '56965': 'Recipe: Savory Thorn Cornbread',
 '27244': 'Crafting Motif 4: Nord Style',
 '126903': 'Praxis: Redoran Urn, Pale Marble',
 '45331': 'Maple Lightning Staff',
 '99283': "Sword-Singer's Ring",
 '99688': "Spinner's Jerkin",
 '175846': "Companion's Breeches",
 '118553': 'Target Skeleton, Humanoid',
 '71199': 'Rough Ruby Ash',
 '147727': 'Crafting Motif 74: Pellitine Staves',
 '165611': 'Vampiric Cabinet, Ornate',
 '26583': 'Glyph 

In [68]:
itemid in new_item_db

True

In [58]:
from bs4 import BeautifulSoup

In [59]:
soup = BeautifulSoup(result.text)

In [62]:
soup.find(id='esoil_rawdata_name').text

"Hrothgar's Shield"

In [ ]:
9391 * 7.5

In [80]:
top200_by_qty= list(qty_df[:200].index)

In [77]:
top200_by_price

['54177',
 '135150',
 '54173',
 '135149',
 '30145',
 '114892',
 '135145',
 '64222',
 '114895',
 '56863',
 '180765',
 '54181',
 '180427',
 '68342',
 '71072',
 '180428',
 '114894',
 '71200',
 '45854',
 '30164',
 '115026',
 '30161',
 '120078',
 '170130',
 '141750',
 '180766',
 '135148',
 '175966',
 '64487',
 '71198',
 '181577',
 '180600',
 '135154',
 '181571',
 '171911',
 '180601',
 '139411',
 '115029',
 '181584',
 '30158',
 '133550',
 '135146',
 '181578',
 '180523',
 '54180',
 '68343',
 '140308',
 '56862',
 '82076',
 '137947',
 '30166',
 '167976',
 '44714',
 '119821',
 '119822',
 '181565',
 '115028',
 '135137',
 '71239',
 '181585',
 '181583',
 '171585',
 '181582',
 '77589',
 '119594',
 '71199',
 '181572',
 '180521',
 '150731',
 '181576',
 '150671',
 '135153',
 '170129',
 '54339',
 '180860',
 '64221',
 '181580',
 '54176',
 '180857',
 '139019',
 '115027',
 '147512',
 '152138',
 '175930',
 '152135',
 '64504',
 '176622',
 '151621',
 '54172',
 '178462',
 '181575',
 '180439',
 '137928',
 '1815

In [81]:
top200_by_qty

['71198',
 '135145',
 '135146',
 '71200',
 '71199',
 '64489',
 '30145',
 '64504',
 '64502',
 '71072',
 '64506',
 '114892',
 '71239',
 '114895',
 '44714',
 '33271',
 '64487',
 '135137',
 '114894',
 '64501',
 '30164',
 '30166',
 '30158',
 '114889',
 '30161',
 '30162',
 '30159',
 '30163',
 '803',
 '30157',
 '30160',
 '77590',
 '54339',
 '45831',
 '54176',
 '45850',
 '114893',
 '54177',
 '30357',
 '42869',
 '114890',
 '75365',
 '77589',
 '30148',
 '33758',
 '5413',
 '135140',
 '42872',
 '76828',
 '76844',
 '77584',
 '45851',
 '44879',
 '27100',
 '54175',
 '77587',
 '54173',
 '54171',
 '27064',
 '27052',
 '33753',
 '135144',
 '46127',
 '27049',
 '27035',
 '45852',
 '30154',
 '135142',
 '30152',
 '46142',
 '30153',
 '26954',
 '54181',
 '27043',
 '794',
 '6001',
 '76827',
 '54172',
 '27038',
 '27057',
 '46129',
 '135161',
 '23121',
 '30165',
 '64509',
 '883',
 '135138',
 '4487',
 '64508',
 '34329',
 '77591',
 '77583',
 '54180',
 '42862',
 '45854',
 '28666',
 '150731',
 '45853',
 '27058',
 '46

In [85]:
top_items = list(set(top200_by_price).union(set(top200_by_qty)))

In [86]:
len(top_items)

355

In [7]:
import json

In [92]:
with open('c:/users/jtern/documents/github/eso_motifs/itemdb.json','w') as f:
    json.dump(new_item_db,f)

In [8]:
with open('c:/users/jtern/documents/github/eso_motifs/itemdb.json','r') as f:
    new_item_db = json.load(f)


In [117]:
qty_df2 = qty_df.reset_index().sort_values(['week_period','quantity'],ascending=[True,False])

In [118]:
qty_df2

week_period item_id   taxes  quantity     price  \
10     2021-08-19/2021-08-25   71072  202713     20988   5792100   
34     2021-08-19/2021-08-25  114892  374737     10254  10707865   
38     2021-08-19/2021-08-25  135146   12609      8854    360478   
50     2021-08-19/2021-08-25   64489    2678      6121     76641   
55     2021-08-19/2021-08-25  135145   40952      5138   1170260   
...                      ...     ...     ...       ...       ...   
10755  2021-09-16/2021-09-22  160791      12         1       350   
10757  2021-09-16/2021-09-22  160793      24         1       700   
10758  2021-09-16/2021-09-22  160831     236         1      6767   
10764  2021-09-16/2021-09-22  176319      23         1       679   
17349  2021-09-16/2021-09-22   99999      42         1      1200   

                    item_name    unitPrice  
10     Alliance Spell Draught   284.608696  
34               Mundane Rune  1031.937149  
38             Platinum Ounce    40.649130  
50             Rubedite Ingot    12.525928  
55              Platinum Dust   228.173103  
...                       ...          ...  
10755                           350.000000  
10757                           700.000000  
10758                          6767.000000  
10764                           679.000000  
17349                          1200.000000  

[17350 rows x 7 columns]

In [119]:
price_df = agg_df.reset_index().sort_values(['week_period','price'],ascending=[True,False])

In [135]:
price_df.head(250)

week_period item_id   taxes  quantity     price  \
8     2021-08-19/2021-08-25  135150  498568        63  14245148   
10    2021-08-19/2021-08-25  114892  374737     10254  10707865   
12    2021-08-19/2021-08-25   54177  341270       526   9751274   
25    2021-08-19/2021-08-25   71072  202713     20988   5792100   
46    2021-08-19/2021-08-25  114895  132590      4678   3788371   
47    2021-08-19/2021-08-25   64222  131449        92   3755883   
52    2021-08-19/2021-08-25  114894  123188      4245   3520113   
57    2021-08-19/2021-08-25  180765  108150         4   3090000   
62    2021-08-19/2021-08-25  181584  104999         3   2999999   
63    2021-08-19/2021-08-25  181571  104745         4   2992720   
67    2021-08-19/2021-08-25   54173  100681       296   2876968   
69    2021-08-19/2021-08-25  181577   99750         2   2850000   
86    2021-08-19/2021-08-25  181585   76324         3   2180719   
89    2021-08-19/2021-08-25  180427   74581         7   2130981   
92    2021-08-19/2021-08-25   68342   72643        57   2075750   
97    2021-08-19/2021-08-25  181582   71224         6   2034999   
99    2021-08-19/2021-08-25  141750   69999         1   1999999   
100   2021-08-19/2021-08-25  181583   69125         3   1975000   
104   2021-08-19/2021-08-25  135149   65096        27   1860100   
120   2021-08-19/2021-08-25  137963   56000         1   1600000   
123   2021-08-19/2021-08-25  140308   56000         1   1600000   
125   2021-08-19/2021-08-25  181580   55679         6   1590888   
129   2021-08-19/2021-08-25  181575   54250         3   1550000   
130   2021-08-19/2021-08-25  175930   52500         1   1500000   
131   2021-08-19/2021-08-25  176015   52500         1   1500000   
132   2021-08-19/2021-08-25  180815   52500         1   1500000   
155   2021-08-19/2021-08-25   30145   47055      3378   1344572   
162   2021-08-19/2021-08-25   45854   44371       334   1268130   
167   2021-08-19/2021-08-25   64487   42393      2577   1211265   
168   2021-08-19/2021-08-25  180600   42000         2   1200000   
169   2021-08-19/2021-08-25  181576   42000         1   1200000   
170   2021-08-19/2021-08-25  180523   42000         1   1200000   
174   2021-08-19/2021-08-25  135145   40952      5138   1170260   
184   2021-08-19/2021-08-25   68343   39805        25   1137975   
186   2021-08-19/2021-08-25  119821   39199         4   1120000   
192   2021-08-19/2021-08-25  180601   38150         3   1090000   
208   2021-08-19/2021-08-25  178463   35875        21   1025000   
213   2021-08-19/2021-08-25  181578   35000         1   1000000   
214   2021-08-19/2021-08-25  152253   35000         1   1000000   
222   2021-08-19/2021-08-25   54181   33975       232    971148   
234   2021-08-19/2021-08-25   82076   32093         2    916998   
245   2021-08-19/2021-08-25  139409   30595        19    874238   
246   2021-08-19/2021-08-25   56863   30528        30    872399   
247   2021-08-19/2021-08-25  137870   30186         6    862500   
252   2021-08-19/2021-08-25  137947   29574         3    845000   
253   2021-08-19/2021-08-25  119594   29574         3    845000   
254   2021-08-19/2021-08-25  119822   29504         3    843000   
260   2021-08-19/2021-08-25   79339   28699         2    819999   
266   2021-08-19/2021-08-25  135148   28035        59    801123   
268   2021-08-19/2021-08-25  180857   28000         1    800000   
269   2021-08-19/2021-08-25  181568   27999         1    799999   
270   2021-08-19/2021-08-25  181574   27999         1    799998   
274   2021-08-19/2021-08-25  180563   27823         2    794988   
293   2021-08-19/2021-08-25  181565   25231         1    720890   
298   2021-08-19/2021-08-25  180689   24500         2    700000   
309   2021-08-19/2021-08-25   54180   23873       506    682367   
317   2021-08-19/2021-08-25  181579   23100         5    660000   
318   2021-08-19/2021-08-25  171917   22977         1    656500   
336   2021-08-19/2021-08-25  120078   21856        11    624713

In [128]:
len(list(price_df.loc[price_df['item_name']=='','item_id'].unique()))

8990

In [125]:
price_df['item_name'].value_counts()

                                       15794
Lightning Staff of Dark Convergence       14
Inferno Staff of Dark Convergence         10
Sealed Blacksmithing Writ                 10
Briarheart Band                           10
                                       ...  
Runebox: Clockwork Reliquary               1
Enervating Poison I                        1
Design: Leyawiin Pie, Octopus              1
Diagram: Dwarven Pew, Refined              1
Companion's Helmet                         1
Name: item_name, Length: 387, dtype: int64

In [131]:
price_df['rank'] = price_df.groupby(['week_period'])['price'].rank('dense',ascending=False)

In [133]:
pd.options.display.max_rows = 999


In [136]:
sales_df.to_pickle('c:/users/jtern/documents/github/eso_motifs/sales_data.pickle')

In [10]:
master_sales_df = pd.read_pickle('c:/users/jtern/documents/github/eso_motifs/sales_data.pickle')

In [7]:
import bisect

In [3]:
multiplier = {750000 : 1.05, 1000000 : 1.1, 1500000 :1.15,3000000 : 1.20,6000000 : 1.25}


In [39]:
bisect.bisect_right(sorted(multiplier.keys()),1000000)

2

In [47]:
tries = [0,100000,750000,900000,1000000,1100000,1500000,1750000,3000000,3500000,6000000,10000000]

In [48]:
for t in tries:
    a = sorted(multiplier.keys())
    mult_ix = bisect.bisect_right(a,t) -1
    if mult_ix <= 0 : mult = 0
    elif mult_ix > len(multiplier.keys()) -1 : mult= multiplier[a[len(a)-1]]
    else : mult = multiplier[a[mult_ix]]
    print(t,mult)
    

0 0
100000 0
750000 0
900000 0
1000000 1.1
1100000 1.1
1500000 1.15
1750000 1.15
3000000 1.2
3500000 1.2
6000000 1.25
10000000 1.25


In [18]:
mult_ix

5

In [24]:
len(multiplier.keys())

5